In [3]:
import pandas as pd
import requests
import numpy as np

def get_historical_prices(stocks, start_date, end_date):
    historical_data = pd.DataFrame()

    for stock in stocks:
        url = f'https://financialmodelingprep.com/api/v3/historical-chart/5min/{stock}?from={start_date}&to={end_date}&apikey=86dd63f6b8ae774b061232685b78eb52'
        response = requests.get(url)
        if response.status_code == 200:
            data = response.json()
            df = pd.DataFrame(data)
            df['date'] = pd.to_datetime(df['date'])
            df.set_index('date', inplace=True)
            df.rename(columns={'close': stock}, inplace=True)
            historical_data = pd.concat([historical_data, df[stock]], axis=1)

    return historical_data

# 定义投资组合的股票及持股数量
portfolio = {
    "TSLA": 400,
    "AAPL": 10,
    "BILI": 40,
    "BRK.B": 10,
    "COIN": 100,
    "IQ": 1000,
    "MSFT": 40,
    "PDD": 20
}

# 定义历史数据的起始日期和结束日期
start_date = "2023-01-01"
end_date = "2023-06-14"

# 获取投资组合的历史价格数据
stocks = list(portfolio.keys())
historical_data = get_historical_prices(stocks, start_date, end_date)

# 计算投资组合的每日收益率
portfolio_returns = historical_data.pct_change()

# 计算风险系数（波动率）
risk_coefficient = np.std(portfolio_returns.sum(axis=1)) * np.sqrt(252)

# 计算未来30天、一个季度、半年和一年的波动百分比
future_periods = [30, 90, 180, 365]
volatility_percentages = []

for period in future_periods:
    future_prices = historical_data.iloc[-1] * (1 + portfolio_returns.mean() * period)
    volatility_percentage = (future_prices - historical_data.iloc[-1]) / historical_data.iloc[-1] * 100
    volatility_percentages.append(volatility_percentage)

# 计算投资组合的年化收益率
portfolio_annual_returns = (1 + portfolio_returns.mean()) ** 252 - 1

# 计算投资组合的年化波动率
portfolio_annual_volatility = np.std(portfolio_returns.sum(axis=1)) * np.sqrt(252)

# 假设无风险利率为0.04（4%），您可以根据需要进行调整
risk_free_rate = 0.04

# 计算投资组合的夏普比率
portfolio_sharpe_ratio = (portfolio_annual_returns - risk_free_rate) / portfolio_annual_volatility

# 打印结果
print("投资组合的风险系数（波动率）：", round(risk_coefficient * 100, 2), "%")
print("未来30天的波动百分比：", round(volatility_percentages[0], 2), "%")
print("未来一个季度的波动百分比：", round(volatility_percentages[1], 2), "%")
print("未来半年的波动百分比：", round(volatility_percentages[2], 2), "%")
print("未来一年的波动百分比：", round(volatility_percentages[3], 2), "%")
print("投资组合的夏普比率：", round(portfolio_sharpe_ratio, 2))

投资组合的风险系数（波动率）： 30.67 %
未来30天的波动百分比： TSLA    -0.89
AAPL    -0.13
BILI    -0.51
BRK.B   -0.18
COIN     0.66
IQ      -0.85
MSFT    -0.13
PDD     -0.66
dtype: float64 %
未来一个季度的波动百分比： TSLA    -2.68
AAPL    -0.39
BILI    -1.52
BRK.B   -0.54
COIN     1.97
IQ      -2.54
MSFT    -0.39
PDD     -1.99
dtype: float64 %
未来半年的波动百分比： TSLA    -5.35
AAPL    -0.79
BILI    -3.03
BRK.B   -1.08
COIN     3.94
IQ      -5.07
MSFT    -0.78
PDD     -3.97
dtype: float64 %
未来一年的波动百分比： TSLA    -10.86
AAPL     -1.60
BILI     -6.15
BRK.B    -2.19
COIN      7.98
IQ      -10.29
MSFT     -1.58
PDD      -8.05
dtype: float64 %
投资组合的夏普比率： TSLA    -0.37
AAPL    -0.17
BILI    -0.27
BRK.B   -0.18
COIN     0.05
IQ      -0.35
MSFT    -0.17
PDD     -0.31
dtype: float64
